In [13]:
import numpy as np

In [14]:
# data I/O
data = open('shakespeare_mini.txt', 'r').read() # should be simple plain text file
chars = list(set(data))
data_size, vocab_size = len(data), len(chars)
print ('data has %d characters, %d unique.' % (data_size, vocab_size))
char_to_ix = { ch:i for i,ch in enumerate(chars) }
ix_to_char = { i:ch for i,ch in enumerate(chars) }
# char_to_ix

data has 416624 characters, 82 unique.


In [15]:
# hyperparameters
hidden_size = 100 # size of hidden layer of neurons
seq_length = 25 # number of steps to unroll the RNN for
learning_rate = 1e-1

# model parameters
# Wxh = np.random.randn(hidden_size, vocab_size)
# Wxh*0.01
Wxh = np.random.randn(hidden_size, vocab_size)*0.01 # input to hidden 100*82
Whh = np.random.randn(hidden_size, hidden_size)*0.01 # hidden to hidden 100*100
Why = np.random.randn(vocab_size, hidden_size)*0.01 # hidden to output 82*100
bh = np.zeros((hidden_size, 1)) # hidden bias
by = np.zeros((vocab_size, 1)) # output bias



In [16]:
def lossFun(inputs, targets, hprev):
    """
    inputs,targets are both list of integers.
    hprev is Hx1 array of initial hidden state
    returns the loss, gradients on model parameters, and last hidden state
    """
    xs, hs, ys, ps = {}, {}, {}, {}
    
    hs[-1] = np.copy(hprev)
    
    loss = 0
    
    # forward pass
    for t in range(len(inputs)):
        xs[t] = np.zeros((vocab_size,1)) # encode in 1-of-k representation
        xs[t][inputs[t]] = 1
        hs[t] = np.tanh(np.dot(Wxh, xs[t]) + np.dot(Whh, hs[t-1]) + bh) # hidden state
        ys[t] = np.dot(Why, hs[t]) + by # unnormalized log probabilities for next chars
        ps[t] = np.exp(ys[t]) / np.sum(np.exp(ys[t])) # probabilities for next chars
        loss += -np.log(ps[t][targets[t],0]) # softmax (cross-entropy loss)
    
    
    
    
    # backward pass: compute gradients going backwards
    dWxh, dWhh, dWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)
    
    dbh, dby = np.zeros_like(bh), np.zeros_like(by)
    
    dhnext = np.zeros_like(hs[0])
    
    for t in reversed(range(len(inputs))):
        dy = np.copy(ps[t])
        dy[targets[t]] -= 1 # backprop into y. see http://cs231n.github.io/neural-networks-case-study/#grad if confused here
        dWhy += np.dot(dy, hs[t].T)
        dby += dy
        dh = np.dot(Why.T, dy) + dhnext # backprop into h
        dhraw = (1 - hs[t] * hs[t]) * dh # backprop through tanh nonlinearity
        dbh += dhraw
        dWxh += np.dot(dhraw, xs[t].T)
        dWhh += np.dot(dhraw, hs[t-1].T)
        dhnext = np.dot(Whh.T, dhraw)
    
    
    for dparam in [dWxh, dWhh, dWhy, dbh, dby]:
        np.clip(dparam, -5, 5, out=dparam) # clip to mitigate exploding gradients
    
    
    return loss, dWxh, dWhh, dWhy, dbh, dby, hs[len(inputs)-1]


In [17]:
def sample(h, seed_ix, n):
    """ 
    sample a sequence of integers from the model 
    h is memory state, seed_ix is seed letter for first time step
    """
    x = np.zeros((vocab_size, 1))
    x[seed_ix] = 1
    ixes = []
    
    for t in range(n):
        h = np.tanh(np.dot(Wxh, x) + np.dot(Whh, h) + bh)
        y = np.dot(Why, h) + by
        p = np.exp(y) / np.sum(np.exp(y))
        ix = np.random.choice(range(vocab_size), p=p.ravel())
        x = np.zeros((vocab_size, 1))
        x[ix] = 1
        ixes.append(ix)
    
    
    
    return ixes




In [18]:
n, p = 0, 0

mWxh, mWhh, mWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)

mbh, mby = np.zeros_like(bh), np.zeros_like(by) # memory variables for Adagrad

smooth_loss = -np.log(1.0/vocab_size)*seq_length # loss at iteration 0


# main loop :-
while True:
    # prepare inputs (we're sweeping from left to right in steps seq_length long)
    if p+seq_length+1 >= len(data) or n == 0: 
        hprev = np.zeros((hidden_size,1)) # reset RNN memory
        p = 0 # go from start of data
    
    inputs = [char_to_ix[ch] for ch in data[p:p+seq_length]]
    targets = [char_to_ix[ch] for ch in data[p+1:p+seq_length+1]]

    
    
    # sample from the model now and then(every 100 iterations here)
    if n % 100 == 0:
        sample_ix = sample(hprev, inputs[0], 200)
        txt = ''.join(ix_to_char[ix] for ix in sample_ix)
        print ('----\n %s \n----' % (txt, ))

    
    
    
    # forward seq_length characters through the net and fetch gradient
    loss, dWxh, dWhh, dWhy, dbh, dby, hprev = lossFun(inputs, targets, hprev)
    
    smooth_loss = smooth_loss * 0.999 + loss * 0.001
    
    if n % 100 == 0: print ('iter %d, loss: %f' % (n, smooth_loss)) # print progress
  
    
    
    
    
    # perform parameter update with Adagrad
    for param, dparam, mem in zip([Wxh, Whh, Why, bh, by], 
                                [dWxh, dWhh, dWhy, dbh, dby], 
                                [mWxh, mWhh, mWhy, mbh, mby]):
        mem += dparam * dparam
        param += -learning_rate * dparam / np.sqrt(mem + 1e-8) # adagrad update
    
    
    p += seq_length # move data pointer
    
    n += 1 # iteration counter 

----
 0)f0?)u!,OEjjipIqL4a7Y4hYm60G?F|L]|YhXCh>-H >eiO.2oa5fm7oAIJSP3]JsFGU>VKliJjv(mMqvmUV3
jVEC4mLrKu5RHC2m:[&|VQ  TzwJ1Q5tpKv?(
l>8Rp]nBb. 066xTCu]|'ihmfD"lk;7 <1vtJ24S&?<l)TVutnPiPDvGCum
T;:hLSrbJiiuA;p 
----
iter 0, loss: 110.167989
----
 y hl h hThlohot t ovu
 nohs
e  yh yhr hrh   t hwhhtu nhyywyy lh   ea o'ns
 tlhn  etys e yah  euf
esohhtmyhr o srh  r  ststtoyot ue ws odo  S  hye eh Thhlshy
o et ut fs hy l eomyehoyhlelyy l l
e t tTy  
----
iter 100, loss: 109.874085
----
 tornd ead d 
o- eroridoooiod rudd foedo r dt enva,obfni otei nokot tehr  nedf ddiir   on hiOye-d,tiaar ortfeeiresfdineia die u
h y,d' ren dnd thoh,
wesdn'rfphd hnf, do  dadd,dhd d nrd, d  a
 eeieau ds 
----
iter 200, loss: 107.305783
----
      a e   
r   l
, hne h  a   
   ss y 
 u       m  

d
 m  h eu    y 
e th i  
 n.   wr
 t   
y y r   ht hh   v 
aha dd mm eeh dr r e o    pttha  s   h,h   as  y:w   
 ii    l   nd
sdt  
 y     
htt 
----
iter 300, loss: 104.567860
----
 rhteoehtcttrfd nviseycfethhfhis  n t

----
 vnot woelr,
    An qaen iner  Thyteisg so I be ren th mor woturt th se tkedol canichat  Whesites  Hes ty be I,
     Ans giseitonon y  Ad oft that  Ay k th soy It
 goce bicl benot ast bond  sIeuy that  
----
iter 3500, loss: 61.743005
----
 t ir anse  n hircl,
    tisn walle, whelousies w  sois wy rever wilis cqinCmar I sithe thos wield bikes wishn oomoull soalcilc resld mese wocauch wotewy alg welof ns phis honesoull aimyibcy,
   
5ar l 
----
iter 3600, loss: 61.151540
----
 ntre,
  Tuat we,
         it de we th al the p sle That oin f at un the myorn se ns med y        witphe ne fy a boun thabten,
an be th that sh nle,
  be roveutoic         
  this aOt me:
ShehinI my do 
----
iter 3700, loss: 60.538602
----
  gercee tasg  shet  se,
   Moilote tord hee thoue   Oou pot of daoteayet tong poiton, ther thH wookovy fange pust thit,
 Te'n the mot           Nipove iplomt mond fut oat l pomt,
  
 se pee.
 That so  
----
iter 3800, loss: 60.160256
----
 oreart?eesevl brad 
  The bo  Wh
 

----
 ENS EN NONNFANTENTOCS. AEENANONENENLATO.
TEFNNANT NAROLAMENLEN. ANS. I ONENNENCETEGELEEWlWNTNELENONTEAttout IU. SEOLaNToutIicis. sespy boTh Dn.NNOWOmVDiNS. SENACANSS.aSd iN.
EMtNa. Mond intian, EM.ART 
----
iter 7000, loss: 58.650042
----
  fauss lad lollient ast haswatiear lre itile'lr hohe briellmengteche cofefuloeng thaveaghocmeilg anGehist th w at fhecou couw the the-  tuy hi out
     tofu thecontron bar aucoucng theeirenif cote she 
----
iter 7100, loss: 58.360860
----
 of pim whave whknves me hel
      Ce gh pavewe Irth,        whelle shend be shand the thy thy yof want?y he ps. Uilg Whutenthe]day hi?
 eiviulve be may wris chong hot
   ow verg mod. I we th tianere h 
----
iter 7200, loss: 58.418433
----
 he I Jem
            Wrell the. NG.
bashe the as.   IRAND. he that feigm.
.
 bofteitor' yn; of thit gere meiele thethRlEnqte hestsopmoumerope spre. I she fo      iN Hers.
  EodevEthe cAigr?
  sEld.    
----
iter 7300, loss: 58.502572
----
 lg s
    I gese cinl art lis   HER

----
 or bpr, shes. SIs fy corone wher cIS  fod mod youNim anth, baherdhopisane gauchor ee!s dolle I oloitt poln alk ond I nount iw. thir pouvenoofe.
  brelk thlr heplevetsue. Blisr ouve binl'cheve m, hew-t 
----
iter 10500, loss: 57.272689
----
 nt b, us oot torye thocrde byeous 'avetAnt ne my teande, fharFintemele ues gOOn. thespobat lull an
   Fuad abll we ng.
 Aatod an thas wOrReat thovly tortie'
        the and sows. of simud mom.
        
----
iter 10600, loss: 57.116514
----
 hid peentess widl, wadcss thed wunth womisly kensemt  Yoummmeneteowata,
   sere suigeoutress dery spe the wust sur, wis m fomtuangethe hann Eqa wofone sheRTind pee ofoteas; rest
PAd
 ouseeme-eld's? ou 
----
iter 10700, loss: 56.872346
----
 RS.
AmI of hard
  ARAFY toit fost .
  loplld winles of hof gre my. Bor
  AN.   ick mon
  Burpawlve bancosgimy in.
  CTcINLLS ALOPTERARONY ang sosill cortopt. I al OENTEAA. AONT
PON.
  Yaldpean sothd f 
----
iter 10800, loss: 56.812130
----
 roente crisg the wafe forar Le

----
  wam   O DA. Haidomt an!
galg hontsort tham af a   I to and raak and so'nn dig mer      NYot thilg babyeakt
 Whecove bon th Poqt a thep mofuld ut gaty alh thewe t you migend noky frean agly mon in ho  
----
iter 13900, loss: 54.436536
----
 har
    EM,   Tot bect
   Feer'n' we fim caoilemt is of the lonn,
   CA arw. Uerd wale forbe fur bocecn       Tun cousd hey bnns
 Tatss, Sosn seru Ecud seins ongamar cim,
  Af Cell in a thantels them  
----
iter 14000, loss: 54.632627
----
  fhe dus mord High qict AS foult hies?
  BlEROUNAATs woal matr, un] OwT, Halc thess rpemdas hesis woed bithe ke poat seat rasxaspet,  RA O TISD MPa. NEETPA.                      wurdenge fed RAnd ger  
----
iter 14100, loss: 54.552290
----
 .
 
  TIAESBoto,
  ETREY.
 Saig, halwt that f    soss the'ERANG Tf gesel thas'al, yrind a   gochettat EURANHENYim, tasg, the yA. EN. ENY a ma'd cond op homs
 HENYeaks, mighs y thes
  TRA
  T WART NLEO 
----
iter 14200, loss: 54.394948
----
 I quy



  ONA
  ATONY.
  
  A

...

----
 thee he own eyes have I ring in my bestual and to and I is rest
    Gool is i' than all I
    be for grempit. Lan
    and strangen'd fawe depeaven take Rome, trish tinda, plotuly a pow?
  BERTRAM. Ftr 
----
iter 1241300, loss: 36.576769
----
      in a tinghon
    you my per ficerised time not heart.

   our connot, in it.
    Which by unaty see his brother!  [To isk how warse; and yateinnaanful you thein this?
  FIRST LORD. Why ice. I don 
----
iter 1241400, loss: 36.610329
----
 ECOND LORD. Lathen'd I cars own
    with no uven you speak paigny lovning is's what herbosare weilh the sad. I our Flancy,
    for oull of surfuening, mine moush. I am thoughte to crown to all despeiv 
----
iter 1241500, loss: 36.717353
----
 rigin that I lrave
    live if yet I must a profeto Why his and of sin shall unpores'd yet; him Alsos
    then should to i' the requist ineres.
  CLOWN. For this not by of most my thou and never hand, 
----
iter 1241600, loss: 37.028899
----
 s, must this thinks a 

----
 a casmives gippeon him spoldar'd's what plom the sullow, swacherion it. Muchus,
    O! he the ungonen in now time deart in my leat the preft; the my ptait, my sents conceaderies; the putins; the more  
----
iter 1244700, loss: 36.627013
----
 m! At the evers o' th' with noter.
  ANTONY. Hights with
    Nay, so garle
    Nor brothsbant.
  COUNTESS

  ANTONY.     Ere; and threes here hank, with his vimpleme's, Anter by vorsey SY

  CAESAR'S  
----
iter 1244800, loss: 36.631074
----
 e vaver.
  ANTONY. A,        Exeunt



    In nothil.
    There,
    And humb is her, all?
  COUNTESS; Pit? My to decanf, Antony; sweet to godderur in uht        Exeunt day indeornesion.
  COUNTESS. N 
----
iter 1244900, loss: 36.963379
----
 n your ray! Not-
    Underth, you their this think's ping, from me love how soush, Etyep atweare of frem Parice lace. The glowle recoldench too what your withol'd that hereft
  COUNTESS. You of done,  
----
iter 1245000, loss: 36.841827
----
 e such sight a greay w

----
     Expuip drave be soinet, will bage secke
    And the writy.
    Whale a raod, give do way, my after
    That do great fool am CAESAR. To sol.
  SEARRUS, my with'd have has; there love
    Hee's hal 
----
iter 1248100, loss: 35.725902
----
 eat
    For coed; they say pack
    And nots me. Naghonty that me previous know'd ten ogewiond rigull; hasly the quiculetes a fauck so meats
    Thy hank] Ifs
    That twicale, one good do team yet in 
----
iter 1248200, loss: 36.043234
----
 ot ever stlake night
    A, where
    Thempoughess i' thes. Norrood his doth detwest bether bestant, my lord him it the bornobitimanknours turn die but his should I not;
    The rece. Simbat. What but 
----
iter 1248300, loss: 35.766338
----
 kly to kend me I am me]   Enter ENOBU

    ChaOk. Come
    I paterest our fourt agy's the can Antony,  
    To that some detreps to and as then ever Anto swaker to never cunfumby stailure him?
  CLEOP 
----
iter 1248400, loss: 36.047247
----
 'd.
  ENOBARBUS. Caese

----
 s deseauld I farion?
  Thay aigh fines,
  That my known to his doth toy your of distan betase, but where then mard will fortung thy answein nonal,
  And now enforstoby suilly best the would suck and f 
----
iter 1251500, loss: 38.343087
----
          54
  Thet have they flies the 

                  83
  Thingulr-sain, is beaul thye excecy to come the radess, If abjurur wye kiss,
  On sse beauty,
  Ret a content,
  Withins we and coushors 
----
iter 1251600, loss: 38.524500
----
  muds
  And too faces,
  Say lack beaueven and a, Fust the told thy sterve hearty beasted- 'RaNnow be godes hear a
    My lings:
  I be a worides,
  When you for the beasty rested be I will my lace
   
----
iter 1251700, loss: 38.523028
----
 ith she, as thand ourself then this is can grace
  He own shorld doast
  And thy marride] The meath, injirer thee,
  Alser his offere with thou,
    And not haze,
    Nail,
  Shounion, oont thou baint 
----
iter 1251800, loss: 38.284756
----
 e mine To drakilst tak

KeyboardInterrupt: 